<a href="https://colab.research.google.com/github/anukvma/group18_email_subject_generation/blob/main/WIP_PK_QnA_BART.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install transformers datasets torch

  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl.metadata (1.8 kB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-manylinu

# Load Dataset from CSV

In [3]:
!git clone https://github.com/anukvma/group18_email_subject_generation


Cloning into 'group18_email_subject_generation'...
remote: Enumerating objects: 157, done.
remote: Counting objects: 100% (157/157), done.
remote: Compressing objects: 100% (145/145), done.
remote: Total 157 (delta 81), reused 33 (delta 8), pack-reused 0 (from 0)
Receiving objects: 100% (157/157), 3.24 MiB | 6.76 MiB/s, done.
Resolving deltas: 100% (81/81), done.


In [50]:
import pandas as pd
df = pd.read_csv('group18_email_subject_generation/sampled_qa_data.csv')
df.drop(columns=['Unnamed: 0', 'unit'], inplace=True)
df.rename(columns={'Q': 'question', 'A': 'answer'}, inplace=True)
df.dropna(inplace=True)
df.head()

question  \
0          What is Q-Learning, and how does it work?   
1  Are there ethical considerations regarding AI-...   
2  Explain the workflow of building a machine lea...   
3  Can logistic regression be used for classes mo...   
4  When does regularization come into play in Mac...   

                                              answer  
0  Q-Learning is a model-free Reinforcement Learn...  
1  Yes, concerns about data privacy, transparency...  
2  The process typically involves importing datas...  
3  No logistic regression cannot be used for clas...  
4  At times when the model begins to underfit or ...

In [51]:
# Convert to Hugging Face Dataset format
from datasets import Dataset
dataset = Dataset.from_pandas(df)

In [52]:
from transformers import BartTokenizer

tokenizer = BartTokenizer.from_pretrained('facebook/bart-base')

def tokenize_function(examples):
    # Tokenize the input (question) and output (answer)
    inputs = tokenizer(examples['question'], padding="max_length", truncation=True, max_length=512)
    outputs = tokenizer(examples['answer'], padding="max_length", truncation=True, max_length=512)
    print(inputs)
    print(outputs)
    # Rename the labels and return as a dictionary
    outputs['labels'] = outputs['input_ids']
    outputs['input_ids'] = inputs['input_ids']
    outputs['attention_mask'] = inputs['attention_mask']

    return outputs

# Tokenize the dataset
tokenized_datasets = dataset.map(tokenize_function, batched=True)

Map:   0%|          | 0/666 [00:00<?, ? examples/s]

{'input_ids': [[0, 2264, 16, 1209, 12, 42489, 6, 8, 141, 473, 24, 173, 116, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 

# Model Training

In [54]:
from transformers import BartForConditionalGeneration, Trainer, TrainingArguments

# Load the BART model
model = BartForConditionalGeneration.from_pretrained('facebook/bart-base')

# Define training arguments
training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=4,
    per_device_eval_batch_size=4,
    num_train_epochs=10,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    save_steps=500,
    save_total_limit=2,
)

# Initialize the Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets,
    eval_dataset=tokenized_datasets,  # Use the same dataset for simplicity, ideally, you should split train and eval
    tokenizer=tokenizer
)

# Start training
trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1494: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'early_stopping': True, 'num_beams': 4, 'no_repeat_ngram_size': 3, 'forced_bos_token_id': 0, 'forced_eos_token_id': 2}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'early_stopping': True, 'num_beams': 4, 'no_repeat_ngram_size': 3, 'forced_bos_token_id': 0, 'forced_eos_token_id': 2}


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'early_stopping': True, 'num_beams': 4, 'no_repeat_ngram_size': 3, 'forced_bos_token_id': 0, 'forced_eos_token_id': 2}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'early_stopping': True, 'num_beams': 4, 'no_repeat_ngram_size': 3, 'forced_bos_token_id': 0, 'forced_eos_token_id': 2}


TrainOutput(global_step=1670, training_loss=0.6013561692066536, metrics={'train_runtime': 1470.4685, 'train_samples_per_second': 4.529, 'train_steps_per_second': 1.136, 'total_flos': 2030422405939200.0, 'train_loss': 0.6013561692066536, 'epoch': 10.0})

# Evaluation and Prediction

In [57]:
# Evaluate the model
results = trainer.evaluate()

# Generate an answer for a new question
def generate_answer(question):
    inputs = tokenizer(question, return_tensors="pt").to(model.device)
    output = model.generate(**inputs, max_length=512)
    return tokenizer.decode(output[0], skip_special_tokens=True)

# Example usaged
new_question = "What is Q-Learning, and how does it work?"
answer = generate_answer(new_question)
print("Generated Answer:", answer)

Generated Answer: Q-Learning is a type of supervised learning that involves training a model on a large dataset of text to understand the context of the text. It is a subset of Q-Machine Learning, where the model learns from the input data and uses it to improve the model’s performance.
